<a href="https://colab.research.google.com/github/AUT-Student/BigData-HW1/blob/main/BigData_HW1_Q1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Libraries

# Download File

In [1]:
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials

# Authenticate and create the PyDrive client
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

id='1-OCBGBtKoY_PadKHcXDyWxHQ2BS8Nulo'
downloaded = drive.CreateFile({'id': id})
downloaded.GetContentFile('hw1.zip')

!unzip hw1.zip

Archive:  hw1.zip
   creating: hw1-files/
   creating: hw1-files/q3/
  inflating: hw1-files/q3/patches.csv  
  inflating: hw1-files/q3/lsh.py     
   creating: hw1-files/q1/
  inflating: hw1-files/q1/dataset1.txt  
   creating: hw1-files/q1/.ipynb_checkpoints/
   creating: hw1-files/q2/
  inflating: hw1-files/q2/games_library.txt  
   creating: hw1-files/.ipynb_checkpoints/


# PySpark Setting

In [3]:
!pip install pyspark
!pip install -q findspark

In [4]:
import findspark
findspark.init()
findspark.find()

'/usr/local/lib/python3.7/dist-packages/pyspark'

In [5]:
from pyspark.sql import SparkSession

spark = SparkSession.builder\
        .master("local")\
        .appName("Colab")\
        .config('spark.ui.port', '4050')\
        .getOrCreate()

In [6]:
spark

# Load Dataset

In [15]:
#df = spark.read.format("csv").option("sep","\t").option("header", False).load("/content/hw1-files/q1/dataset1.txt")

In [86]:
def convert_string_to_list(string):
  if string=="":
    return []
  else:
    return [int(item) for item in string.split(",")]

In [87]:
import pandas as pd
df = pd.read_csv("/content/hw1-files/q1/dataset1.txt", sep="\t",names=["id", "friend_id"])

In [88]:
df = df.fillna("")
df["friend_id"] = df["friend_id"].apply(convert_string_to_list)

In [142]:
rdd=spark.sparkContext.parallelize(df.to_dict('records'), 2)

In [143]:
def map_function(item):
  fids = item["friend_id"]

  output = []
  for fid1 in fids:
    for fid2 in fids:
      key = (fid1, fid2)
      value = 1
      output.append((key, value))
  return output

In [144]:
def reduce_function(value1, value2):
  return value1 + value2  

In [168]:
def map_function(item):
  fids = sorted(item["friend_id"])
  output = []
    
  for fid1 in fids:
    counter = {}
    for fid2 in fids:

      if fid1 != fid2:
        counter[fid2] = 1
    
    output.append((fid1, counter))

  return output

In [169]:
from heapq import merge

def reduce_function(value1, value2):
  merged_ids = list(merge(value1.keys(), value2.keys()))

  merged_value = {}
  for id in merged_ids:
    merged_value[id] = value1.get(id, 0) + value2.get(id, 0)

  return merged_value

In [170]:
mapped_rdd = rdd.flatMap(map_function)

In [171]:
reduced_rdd = mapped_rdd.reduceByKey(reduce_function)

In [184]:
output_rdd = reduced_rdd.collect()

In [187]:
output_rdd[0]

(52,
 {0: 3,
  1: 3,
  2: 1,
  3: 1,
  4: 1,
  5: 1,
  6: 2,
  7: 1,
  8: 1,
  9: 1,
  10: 1,
  11: 1,
  12: 1,
  13: 1,
  14: 1,
  15: 1,
  16: 1,
  17: 1,
  18: 1,
  19: 1,
  20: 2,
  21: 2,
  22: 1,
  23: 1,
  24: 1,
  25: 1,
  26: 1,
  27: 1,
  28: 1,
  29: 1,
  30: 1,
  31: 1,
  32: 1,
  33: 1,
  34: 1,
  35: 1,
  36: 1,
  37: 1,
  38: 1,
  39: 1,
  40: 1,
  41: 1,
  42: 1,
  43: 1,
  44: 1,
  45: 1,
  46: 1,
  47: 1,
  48: 1,
  49: 1,
  50: 1,
  51: 1,
  53: 2,
  54: 1,
  55: 1,
  56: 1,
  57: 1,
  58: 1,
  59: 1,
  60: 1,
  61: 1,
  62: 1,
  63: 2,
  64: 1,
  65: 2,
  66: 1,
  67: 1,
  68: 1,
  69: 2,
  70: 1,
  71: 1,
  72: 1,
  73: 2,
  74: 2,
  75: 1,
  76: 1,
  77: 1,
  78: 1,
  79: 1,
  80: 1,
  81: 1,
  82: 1,
  83: 1,
  84: 1,
  85: 1,
  86: 1,
  87: 1,
  88: 1,
  89: 1,
  90: 1,
  91: 2,
  92: 1,
  93: 2,
  94: 1,
  102: 1,
  106: 1,
  154: 1,
  171: 2,
  186: 1,
  204: 2,
  233: 1,
  338: 1,
  347: 1,
  351: 4,
  354: 1,
  362: 1,
  450: 1,
  455: 1,
  457: 1,
  503: 2,

In [195]:
output_rdd[0][0]

52

[15289,
 351,
 1357,
 2554,
 4717,
 5928,
 17880,
 18576,
 20497,
 29827,
 30269,
 43107,
 0,
 1,
 2523,
 2786,
 4981,
 5049,
 5057,
 5933,
 9105,
 11398,
 12640,
 12667,
 13166,
 14238,
 14242,
 14246,
 15285,
 20500,
 20546,
 21170,
 22773,
 23508,
 28884,
 34190,
 34205,
 34466,
 40437,
 41628,
 41784,
 44358,
 6,
 20,
 21,
 53,
 63,
 65,
 69,
 73,
 74,
 91,
 93,
 171,
 204,
 503,
 543,
 546,
 575,
 1230,
 1245,
 1249,
 1417,
 2204,
 2442,
 2687,
 2789,
 2793,
 2864,
 2921,
 2922,
 3435,
 3576,
 3577,
 5058,
 5075,
 5178,
 5179,
 5181,
 5188,
 5670,
 5948,
 5955,
 6783,
 7569,
 8760,
 8790,
 9099,
 9281,
 9467,
 9784,
 9841,
 9847,
 9969,
 9980,
 10469,
 10477,
 10500,
 10698,
 11208,
 11400,
 11404,
 11413,
 12645,
 13034,
 13280,
 13618,
 13650,
 13654,
 13805,
 13854,
 14005,
 14015,
 14105,
 14204,
 14271,
 14569,
 14691,
 14746,
 14969,
 15207,
 15305,
 15306,
 15307,
 15314,
 15715,
 16027,
 16267,
 16539,
 17349,
 17809,
 17888,
 18100,
 18285,
 18306,
 18320,
 18327,
 18456,

array([list([21, 0, 63, 67, 1196, 1814, 2006, 2791, 2897, 3400, 4264, 5038, 5148, 9504, 9822, 12640, 13650, 13655, 13889, 14049, 14391, 14969, 15285, 17880, 18283, 18294, 18581, 18614, 18654, 19513, 20567, 20615, 21163, 21565, 28332, 29382, 30691, 34280, 35533, 38626, 40300, 40429, 40472, 41628, 41767, 42013, 42699, 43892, 44359, 46050, 48736])],
      dtype=object)

In [199]:
output_rdd

[(52,
  {0: 3,
   1: 3,
   2: 1,
   3: 1,
   4: 1,
   5: 1,
   6: 2,
   7: 1,
   8: 1,
   9: 1,
   10: 1,
   11: 1,
   12: 1,
   13: 1,
   14: 1,
   15: 1,
   16: 1,
   17: 1,
   18: 1,
   19: 1,
   20: 2,
   21: 2,
   22: 1,
   23: 1,
   24: 1,
   25: 1,
   26: 1,
   27: 1,
   28: 1,
   29: 1,
   30: 1,
   31: 1,
   32: 1,
   33: 1,
   34: 1,
   35: 1,
   36: 1,
   37: 1,
   38: 1,
   39: 1,
   40: 1,
   41: 1,
   42: 1,
   43: 1,
   44: 1,
   45: 1,
   46: 1,
   47: 1,
   48: 1,
   49: 1,
   50: 1,
   51: 1,
   53: 2,
   54: 1,
   55: 1,
   56: 1,
   57: 1,
   58: 1,
   59: 1,
   60: 1,
   61: 1,
   62: 1,
   63: 2,
   64: 1,
   65: 2,
   66: 1,
   67: 1,
   68: 1,
   69: 2,
   70: 1,
   71: 1,
   72: 1,
   73: 2,
   74: 2,
   75: 1,
   76: 1,
   77: 1,
   78: 1,
   79: 1,
   80: 1,
   81: 1,
   82: 1,
   83: 1,
   84: 1,
   85: 1,
   86: 1,
   87: 1,
   88: 1,
   89: 1,
   90: 1,
   91: 2,
   92: 1,
   93: 2,
   94: 1,
   102: 1,
   106: 1,
   154: 1,
   171: 2,
   186: 1,
   204: 2

In [214]:
def suggest_new_friend(id, number_top):
  exist_friend_id = df[df["id"]==id]["friend_id"].values

  for item in output_rdd:
    if item[0]==id:
      counter = item[1]
      break

  sorted_new_friend = sorted(counter, key=counter.get, reverse=True)

  suggestion_list = []

  for new_id in sorted_new_friend:
    if new_id not in exist_friend_id:
      suggestion_list.append(new_id)
      if len(suggestion_list) == number_top:
        break

  return suggestion_list

# Example

In [217]:
for id in [98, 135, 117, 911, 8814]:
  print(f"id = {id}")
  print(f"Suggestion = {suggest_new_friend(id,10)}\n")

id = 98
Suggestion = [575, 18560, 2554, 13654, 16324, 16350, 30134, 30691, 17, 113]

id = 135
Suggestion = [117, 13792, 33060, 112, 629, 5490, 19091, 19114, 19217, 24568]

id = 117
Suggestion = [135, 34164, 12519, 13793, 15314, 19063, 23507, 23510, 25256, 34140]

id = 911
Suggestion = [913, 24456, 39540, 40560, 919, 30984, 30993, 30995, 30996, 33333]

id = 8814
Suggestion = [8783, 13280, 18099, 18614, 35799, 35800, 7679, 7882, 8797, 8798]

